<a href="https://colab.research.google.com/github/akinprism/eth-anomaly/blob/main/Eth_Transaction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**ETH Transactions Datasets**

## Eth Fraud Detection Dataset
1. https://www.kaggle.com/datasets/vagifa/ethereum-frauddetection-dataset

- ./MyDriver/Colab Notebooks/ethDatasets/transaction_dataset.csv

> *Reference Notebooks*

> - https://www.kaggle.com/code/emanelbendary/fraud-transaction


## Eth Ilicit Features
2. https://www.kaggle.com/datasets/gescobero/ethereum-fraud-dataset

- ./MyDriver/Colab Notebooks/ethDatasets/eth_ilicit_features.csv

## Eth BigQuery Dataset

[About Dataset](https://medium.com/google-cloud/full-relational-diagram-for-ethereum-public-data-on-google-bigquery-2825fdf0fb0b)

3. https://www.kaggle.com/datasets/bigquery/ethereum-blockchain/data?select=traces

 **Library Installation**

In [ ]:
# @title Installations
!pip install --upgrade google-cloud-bigquery
!pip install ggplot
!pip install plotnine

In [ ]:
# @title Drive Mount
from google.colab import drive

drive.mount('/content/drive')

In [100]:
# @title Imports
import os
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from google.cloud import bigquery
from google.cloud.bigquery import Client
from dataclasses import dataclass
import pandas as pd
from plotnine import ggplot, aes, geom_histogram, theme_light, labs, facet_wrap, ggtitle

**Helper Functions**

In [101]:
# @title Helper Functions
from typing import List

def read_csv_from_drive(file_path: str):
    """
    Reads a CSV file from Google Drive and returns it as a pandas DataFrame.

    Args:
        file_path (str): The file path within Google Drive.

    Returns:
        pd.DataFrame: The DataFrame containing the CSV data.
    """
    # Mount Google Drive
    drive.mount('/content/drive')

    # Read the CSV file into a DataFrame
    df = pd.read_csv(file_path, index_col=False)

    return df


@dataclass
class BigQuerySql:
    """SQL statements data class"""
    eth_transactions: str = """SELECT * FROM `your-project-id.your-dataset.your-table` LIMIT 10"""

    def query_sql(self, sql_query_type: str, big_query_client: bigquery.Client):
        """Query function for big queries"""
        sql = getattr(self, sql_query_type)
        return big_query_client.query(sql)


def plot_columns(dataset: pd.DataFrame, columns_to_plot: List[str]):
  """Plot columns of the dataset"""
  for column in columns_to_plot:
      plot = (
          ggplot(dataset[columns_to_plot], aes(x=column)) +
          geom_histogram(binwidth=0.5, fill='#5DADE2', color='#21618C') +
          theme_light() +
          aes(y='stat(count)') +
          labs(title=f'Distribution of {column}')
      )
      print(plot)


In [ ]:
# @title Read Datasets
# Usage example:
transaction_eth_file_path = '/content/drive/MyDrive/Colab Notebooks/ethDatasets/transaction_dataset.csv'
eth_illicit_features = '/content/drive/MyDrive/Colab Notebooks/ethDatasets/eth_illicit_features.csv'


transaction_eth_dataset = read_csv_from_drive(transaction_eth_file_path)
eth_illicity_features_dataset = read_csv_from_drive(eth_illicit_features)

In [107]:
# @title Preprocess Datasets
# Preprocess
transaction_eth_dataset.drop("Unnamed: 0", axis=1, inplace=True)
transaction_eth_dataset.drop("Index", axis=1, inplace=True)

In [108]:
# @title Standardise the Columns of Datasets
# Mapping for Dataset 1 (eth_illicity_features_dataset)
mapping_dataset1 = {
    'address': 'address',
    'flag': 'is_fraudulent',
    'minTimeBetweenSentTnx': 'min_time_between_sent_tx',
    'maxTimeBetweenSentTnx': 'max_time_between_sent_tx',
    'avgTimeBetweenSentTnx': 'avg_time_between_sent_tx',
    'minTimeBetweenRecTnx': 'min_time_between_received_tx',
    'maxTimeBetweenRecTnx': 'max_time_between_received_tx',
    'avgTimeBetweenRecTnx': 'avg_time_between_received_tx',
    'lifetime': 'account_lifetime',
    'sentTransactions': 'sent_transactions_count',
    'receivedTransactions': 'received_transactions_count',
    'createdContracts': 'created_contracts_count',
    'numUniqSentAddress': 'unique_sent_addresses_count',
    'numUniqRecAddress': 'unique_received_addresses_count',
    'minValSent': 'min_value_sent',
    'maxValSent': 'max_value_sent',
    'avgValSent': 'avg_value_sent',
    'minValReceived': 'min_value_received',
    'maxValReceived': 'max_value_received',
    'avgValReceived': 'avg_value_received',
    'totalTransactions': 'total_transactions_count',
    'totalEtherSent': 'total_ether_sent',
    'totalEtherReceived': 'total_ether_received',
    'totalEtherSentContracts': 'total_ether_sent_to_contracts',
    'totalEtherBalance': 'total_ether_balance',
    # ... add other columns as needed
    'activityDays': 'activity_days',
    'dailyMax': 'daily_max',
    'ratioRecSent': 'ratio_received_to_sent',
    'ratioSentTotal': 'ratio_sent_to_total',
    'ratioRecTotal': 'ratio_received_to_total',
    'giniSent': 'gini_coefficient_sent',
    'giniRec': 'gini_coefficient_received',
    'txFreq': 'transaction_frequency',
    'stdBalanceEth': 'std_deviation_balance_ether'
}

# Mapping for Dataset 2 (transaction_eth_dataset)
mapping_dataset2 = {
    'Address': 'address',
    'FLAG': 'is_fraudulent',
    'Avg min between sent tnx': 'min_time_between_sent_tx',
    'Avg min between received tnx': 'avg_time_between_received_tx',
    'Time Diff between first and last (Mins)': 'account_lifetime',
    'Sent tnx': 'sent_transactions_count',
    'Received Tnx': 'received_transactions_count',
    'Number of Created Contracts': 'created_contracts_count',
    'Unique Sent To Addresses': 'unique_sent_addresses_count',
    'Unique Received From Addresses': 'unique_received_addresses_count',
    'min value received': 'min_value_received',
    'max value received': 'max_value_received',
    'avg val received': 'avg_value_received',
    'min val sent': 'min_value_sent',
    'max val sent': 'max_value_sent',
    'avg val sent': 'avg_value_sent',
    'min value sent to contract': 'min_value_sent_to_contract',
    'max val sent to contract': 'max_value_sent_to_contract',
    'avg value sent to contract': 'avg_value_sent_to_contract',
    'total transactions (including tnx to create contract': 'total_transactions_count',
    'total Ether sent': 'total_ether_sent',
    'total ether received': 'total_ether_received',
    'total ether sent contracts': 'total_ether_sent_to_contracts',
    'total ether balance': 'total_ether_balance',
    # ... add other columns as needed
    ' Total ERC20 tnxs': 'total_erc20_transactions',
    ' ERC20 total Ether received': 'erc20_total_ether_received',
    ' ERC20 total ether sent': 'erc20_total_ether_sent',
    ' ERC20 total Ether sent contract': 'erc20_total_ether_sent_to_contract',
    ' ERC20 uniq sent addr': 'erc20_unique_sent_addresses_count',
    ' ERC20 uniq rec addr': 'erc20_unique_received_addresses_count',
    ' ERC20 uniq sent addr.1': 'erc20_unique_sent_addresses_1_count',
    ' ERC20 uniq rec contract addr': 'erc20_unique_received_contract_addresses_count',
    ' ERC20 avg time between sent tnx': 'erc20_avg_time_between_sent_tx',
    ' ERC20 avg time between rec tnx': 'erc20_avg_time_between_received_tx',
    ' ERC20 avg time between rec 2 tnx': 'erc20_avg_time_between_received_2_tx',
    ' ERC20 avg time between contract tnx': 'erc20_avg_time_between_contract_tx',
    ' ERC20 min val rec': 'erc20_min_value_received',
    ' ERC20 max val rec': 'erc20_max_value_received',
    ' ERC20 avg val rec': 'erc20_avg_value_received',
    ' ERC20 min val sent': 'erc20_min_value_sent',
    ' ERC20 max val sent': 'erc20_max_value_sent',
    ' ERC20 avg val sent': 'erc20_avg_value_sent',
    ' ERC20 min val sent contract': 'erc20_min_value_sent_to_contract',
    ' ERC20 max val sent contract': 'erc20_max_value_sent_to_contract',
    ' ERC20 avg val sent contract': 'erc20_avg_value_sent_to_contract',
    ' ERC20 uniq sent token name': 'erc20_unique_sent_token_names_count',
    ' ERC20 uniq rec token name': 'erc20_unique_received_token_names_count',
    ' ERC20 most sent token type': 'erc20_most_sent_token_type',
    ' ERC20_most_rec_token_type': 'erc20_most_received_token_type'
}

# Rename columns
eth_illicity_features_dataset.rename(columns=mapping_dataset1, inplace=True)
transaction_eth_dataset.rename(columns=mapping_dataset2, inplace=True)


In [109]:
# @title Check Missing Values and Columns of Two Datasets
# 4. Missing values -> Transaction ETH Dataset
print("\n\n --------------------- \n\n")

missing_values = transaction_eth_dataset.isnull().sum()
print("Missing values for each column [TRANSACTION ETH DATASETS]: \n")
print(missing_values)

print("\n\n --------------------- \n\n")

# 4. Missing values -> ETH Illicit Dataset
missing_values = eth_illicity_features_dataset.isnull().sum()
print("Missing values for each column [ILLICITY FEATURES DATASET]: \n")
print(missing_values)



 --------------------- 


Missing values for each column [TRANSACTION ETH DATASETS]: 

address                                             0
is_fraudulent                                       0
min_time_between_sent_tx                            0
avg_time_between_received_tx                        0
account_lifetime                                    0
sent_transactions_count                             0
received_transactions_count                         0
created_contracts_count                             0
unique_received_addresses_count                     0
unique_sent_addresses_count                         0
min_value_received                                  0
max value received                                  0
avg_value_received                                  0
min_value_sent                                      0
max_value_sent                                      0
avg_value_sent                                      0
min_value_sent_to_contract                     

**Shared Column List**
address \
is_fraudulent \
min_time_between_sent_tx  \
max_time_between_sent_tx  \
avg_time_between_sent_tx  \
min_time_between_received_tx  \
max_time_between_received_tx  \
avg_time_between_received_tx  \
account_lifetime  \
sent_transactions_count  \
received_transactions_count  \
created_contracts_count \
unique_sent_addresses_count  \
unique_received_addresses_count  \
min_value_sent  \
max_value_sent  \
avg_value_sent  \
min_value_received \
max_value_received \
avg_value_received \
total_transactions_count \
total_ether_sent \
total_ether_received \
total_ether_sent_to_contracts \
total_ether_balance \

In [110]:
transaction_eth_dataset.head()

address  is_fraudulent  \
0  0x00009277775ac7d0d59eaad8fee3d10ac6c805e8              0   
1  0x0002b44ddb1476db43c868bd494422ee4c136fed              0   
2  0x0002bda54cb772d040f779e88eb453cac0daa244              0   
3  0x00038e6ba2fd5c09aedb96697c8d7b8fa6632e5e              0   
4  0x00062d1dd1afb6fb02540ddad9cdebfe568e0d89              0   

   min_time_between_sent_tx  avg_time_between_received_tx  account_lifetime  \
0                    844.26                       1093.71         704785.63   
1                  12709.07                       2958.44        1218216.73   
2                 246194.54                       2434.02         516729.30   
3                  10219.60                      15785.09         397555.90   
4                     36.61                      10707.77         382472.42   

   sent_transactions_count  received_transactions_count  \
0                      721                           89   
1                       94                            8   
2                        2                           10   
3                       25                            9   
4                     4598                           20   

   created_contracts_count  unique_received_addresses_count  \
0                        0                               40   
1                        0                                5   
2                        0                               10   
3                        0                                7   
4                        1                                7   

   unique_sent_addresses_count  ...  erc20_min_value_sent  \
0                          118  ...              0.000000   
1                           14  ...              2.260809   
2                            2  ...              0.000000   
3                           13  ...            100.000000   
4                           19  ...              0.000000   

   erc20_max_value_sent  erc20_avg_value_sent  \
0          1.683100e+07         271779.920000   
1          2.260809e+00              2.260809   
2          0.000000e+00              0.000000   
3          9.029231e+03           3804.076893   
4          4.500000e+04          13726.659220   

   erc20_min_value_sent_to_contract  erc20_max_value_sent_to_contract  \
0                               0.0                               0.0   
1                               0.0                               0.0   
2                               0.0                               0.0   
3                               0.0                               0.0   
4                               0.0                               0.0   

   erc20_avg_value_sent_to_contract  erc20_unique_sent_token_names_count  \
0                               0.0                                 39.0   
1                               0.0                                  1.0   
2                               0.0                                  0.0   
3                               0.0                                  1.0   
4                               0.0                                  6.0   

   erc20_unique_received_token_names_count  erc20_most_sent_token_type  \
0                                     57.0                   Cofoundit   
1                                      7.0              Livepeer Token   
2                                      8.0                        None   
3                                     11.0                      Raiden   
4                                     27.0               StatusNetwork   

   erc20_most_received_token_type  
0                       Numeraire  
1                  Livepeer Token  
2                           XENON  
3                           XENON  
4                             EOS  

[5 rows x 49 columns]

In [111]:
eth_illicity_features_dataset.head()

address  is_fraudulent  \
0  0xd0cc2b24980cbcca47ef755da88b220a82291407              1   
1  0x4cdc1cba0aeb5539f2e0ba158281e67e0e54a9b1              1   
2  0x00e01a648ff41346cdeb873182383333d2184dd1              1   
3  0x858457daa7e087ad74cdeeceab8419079bc2ca03              1   
4  0x240e125c20a4cc84bd6e7f8d1fd07aff4c06d43d              1   

   min_time_between_sent_tx  max_time_between_sent_tx  \
0                       0.0                 2387389.0   
1                       0.0                       0.0   
2                      37.0                25112882.0   
3                       0.0                  642460.0   
4                       0.0                       0.0   

   avg_time_between_sent_tx  min_time_between_received_tx  \
0              5.807655e+04                          89.0   
1              0.000000e+00                     3021091.0   
2              1.710279e+06                           0.0   
3              1.576106e+04                           0.0   
4              0.000000e+00                        3894.0   

   max_time_between_received_tx  avg_time_between_received_tx  \
0                  1.501076e+09                  7.148260e+07   
1                  1.502802e+09                  7.529115e+08   
2                  1.500397e+09                  6.820612e+07   
3                  1.500037e+09                  1.352571e+07   
4                  1.500402e+09                  3.751409e+08   

   account_lifetime  sent_transactions_count  ...  total_ether_balance  \
0                46                       66  ...             0.291940   
1                35                        0  ...             0.013541   
2               299                       15  ...             0.266494   
3                36                      109  ...             0.007419   
4                82                        1  ...             0.002199   

   activity_days  daily_max  ratio_received_to_sent  ratio_sent_to_total  \
0             10         60                0.313433             0.750000   
1              2          1                2.000000             0.000000   
2             14         16                1.375000             0.394737   
3             36         67                1.009091             0.493213   
4              3          3                2.000000             0.166667   

   ratio_received_to_total  gini_coefficient_sent  gini_coefficient_received  \
0                 0.238636               0.969121                   0.888782   
1                 0.666667               0.000000                   0.238480   
2                 0.578947               0.465450                   0.614205   
3                 0.502262               0.957906                   0.794121   
4                 0.666667               0.000000                   0.406556   

   transaction_frequency  std_deviation_balance_ether  
0               1.891304                   147.701484  
1               0.057143                     0.005000  
2               0.123746                    52.129575  
3               6.111111                   233.689231  
4               0.060976                     0.757788  

[5 rows x 34 columns]

In [113]:
# @title Common Attributes Between Two Datasets
common_addresses = set(transaction_eth_dataset["address"]).intersection(set(eth_illicity_features_dataset["address"]))

print(f"Total Addresses ETH dataset: {len(set(transaction_eth_dataset['address']))}")
print(f"Flag ETH dataset 1: {len(transaction_eth_dataset[transaction_eth_dataset['is_fraudulent'] == 1])}")

print(f"Total Addresses Illicit dataset: {len(set(eth_illicity_features_dataset['address']))}")
print(f"Flag ETH dataset 1: {len(eth_illicity_features_dataset[eth_illicity_features_dataset['is_fraudulent'] == 1])}")

print(f"Number of common addresses: {len(common_addresses)}")
# If you want to see the actual common addresses:
# print(common_addresses)

Total Addresses ETH dataset: 9816
Flag ETH dataset 1: 2179
Total Addresses Illicit dataset: 12146
Flag ETH dataset 1: 5150
Number of common addresses: 1660


In [117]:
# @title Importance Analysis on "Transaction ETH Dataset"
from sklearn.ensemble import RandomForestClassifier
import matplotlib.pyplot as plt

# Assuming transaction_eth_dataset is already loaded
# Handle missing values if any (for simplicity, we'll drop them here)
transaction_eth_dataset = transaction_eth_dataset.dropna()

# Split data into features and target
X = transaction_eth_dataset.drop(columns=['is_fraudulent', 'address'])  # Drop non-feature columns
y = transaction_eth_dataset['is_fraudulent']

# Train a Random Forest Classifier
clf = RandomForestClassifier(n_estimators=100)

# Identify non-numeric columns
non_numeric_cols = X.select_dtypes(include=['object']).columns
print("Non-numeric columns:", non_numeric_cols)

# For simplicity, let's one-hot encode these columns
X = pd.get_dummies(X, columns=non_numeric_cols, drop_first=True)


clf.fit(X, y)

# Extract feature importances
feature_importances = clf.feature_importances_

# Create a DataFrame for visualization
features_df = pd.DataFrame({
    'Feature': X.columns,
    'Importance': feature_importances
})

# Sort the DataFrame by importance
features_df = features_df.sort_values(by='Importance', ascending=False)

# Plot
plt.figure(figsize=(50, 150))
plt.barh(features_df['Feature'], features_df['Importance'])
plt.xlabel('Importance')
plt.ylabel('Feature')
plt.title('Feature Importance for Fraud Detection')
plt.gca().invert_yaxis()  # To display the most important feature at the top
plt.show()

Non-numeric columns: Index(['erc20_most_sent_token_type', 'erc20_most_received_token_type'], dtype='object')
